In [159]:
import folium
from folium.plugins import MarkerCluster
from folium.plugins import FastMarkerCluster
from folium.plugins import HeatMap
import os
import pandas as pd
import geopandas as gpd
import requests
import zipfile
import branca
import branca.colormap as cm

In [47]:
try:
    os.chdir("C:/users/claudio.pacheco/documents/GitHub/economia/mapa_gro")
except:
    os.chdir("C:/users/claud/documents/GitHub/economia/mapa_gro")

### Establecer función de descarga

In [48]:
def download_and_extract(url, filename, check_file_path, extract_path):
    # Checar si el archivo ya existe
    if os.path.isfile(check_file_path):
        print(f"El archivo {filename} existe, no se descargará.")
    else:
        print(f"El archivo {filename} no existe. Descargando.")
        response = requests.get(url)
        with open(filename, "wb") as code:
            code.write(response.content)
        
        # extraer zip
        with zipfile.ZipFile(filename, "r") as zip_ref:
            zip_ref.extractall(extract_path)
        
        # Eliminar zip
        os.remove(filename)

### Descargas
#### Denue

In [49]:
# Lista de archivos para descargar
files_to_download = [
    {
        "url": "https://www.inegi.org.mx/contenidos/masiva/denue/denue_00_72_1_csv.zip",
        "filename": "denue_inegi_72_1_csv.zip",
        "check_file_path": "conjunto_de_datos/denue_inegi_72_1.csv"
    },
    {
        "url": "https://www.inegi.org.mx/contenidos/masiva/denue/denue_00_72_2_csv.zip",
        "filename": "denue_inegi_72_2_csv.zip",
        "check_file_path": "conjunto_de_datos/denue_inegi_72_2.csv"
    }
]
for file in files_to_download:
    download_and_extract(file["url"], file["filename"], file["check_file_path"], os.getcwd())

El archivo denue_inegi_72_1_csv.zip existe, no se descargará.
El archivo denue_inegi_72_2_csv.zip existe, no se descargará.


In [50]:
#Lectura de datos de hoteles
#Identificar los archivos csv
archivos=os.listdir("conjunto_de_datos")
archivos

['denue_inegi_72_1.csv', 'denue_inegi_72_2.csv']

#### Censo 2020 a nivel manzana

In [51]:
#Crear carpeta manzanas
if not os.path.exists("manzanas"):
    os.makedirs("manzanas")
# Lectura de datos de manzanas
descarga_manzanas=[{"url": "https://www.inegi.org.mx/contenidos/programas/ccpv/2020/microdatos/ageb_manzana/RESAGEBURB_12_2020_csv.zip",
                     "filename": "RESAGEBURB_12_2020_csv.zip",
                        "check_file_path": "manzanas/conjunto_de_datos/RESAGEBURB_12_2020.CSV",
                        "extract_path": "manzanas"},
                    {"url": "https://www.inegi.org.mx/contenidos/productos/prod_serv/contenidos/espanol/bvinegi/productos/geografia/marcogeo/889463807469/12_guerrero.zip",
                        "filename": "12_guerrero.zip",
                        "check_file_path": "manzanas/conjunto_de_datos/12m.shp",
                        "extract_path": "manzanas"}]
for file in descarga_manzanas:
    download_and_extract(file["url"], file["filename"], file["check_file_path"], file["extract_path"])

El archivo RESAGEBURB_12_2020_csv.zip no existe. Descargando.
El archivo 12_guerrero.zip existe, no se descargará.


#### Marginación a nivel colonia

In [52]:
if not os.path.exists("margina"):
    os.makedirs("margina")

    download_and_extract("http://www.conapo.gob.mx/work/models/CONAPO/Marginacion/Datos_Abiertos/Colonia/imc2020_shp.zip", "imc2020_shp.zip", "margina/IMC2020.shp", "margina")

### Procesamiento de datos

In [53]:
#Pegar los archvios en un solo dataframe
df=pd.DataFrame()
for i in archivos:
    df=pd.concat([df,pd.read_csv("conjunto_de_datos/"+i,encoding="latin-1")],axis=0)


#Columnas en minúsculas
df.columns=[i.lower() for i in df.columns]
#Filtrar Guerrero
df=df[df["entidad"]=="GUERRERO"]
#Crear columna con los tres primeros  elementos de codigo_act
df["sector"]=df["codigo_act"].apply(lambda x: str(x)[:3])
#Filtrar sector "721"
df=df[df["sector"]=="721"]
#Filtrar municipios de Acapulco de Juárez, Coyuca de Benítez, Atoyac de Álvarez, Benito Juárez, Técpan de Galeana, Xalpatláhuac
df=df[df["municipio"].isin(["Acapulco de Juárez","Coyuca de Benítez","Atoyac de Álvarez","Benito Juárez","Técpan de Galeana",
                            "San Marcos", "Florencio Villarreal","Petatlán", "Zihuatanejo de Azueta","San Miguel Totolapan", "Ajuchitlán del Progreso"])]

df


C:\Users\claud\AppData\Local\Temp\ipykernel_31912\1031254924.py:4: DtypeWarning: Columns (35) have mixed types. Specify dtype option on import or set low_memory=False.
  df=pd.concat([df,pd.read_csv("conjunto_de_datos/"+i,encoding="latin-1")],axis=0)
C:\Users\claud\AppData\Local\Temp\ipykernel_31912\1031254924.py:4: DtypeWarning: Columns (35) have mixed types. Specify dtype option on import or set low_memory=False.
  df=pd.concat([df,pd.read_csv("conjunto_de_datos/"+i,encoding="latin-1")],axis=0)


id                          clee  \
198331  6327488  12001721112001923010000000U7   
198332  6260330  12001721210000011000000000U4   
198337  6202339  12001721111001006001004793S3   
198338  1416927  12001531311001032011000000U5   
198339  1410871  12001531311000763011000000U6   
...         ...                           ...   
220848  6260576  12038721190000261000000000U1   
220849  6260289  12038721190000201001000000U7   
220850  9284380  12038721111000751000000000U0   
220868  6327422  12001721111000523000000000U8   
220872  6717431  12038721111000693001000000U1   

                                                nom_estab  \
198331                ACAPULCO PARK HOTEL & TENNIS CENTER   
198332                              ACAPULCO TRAILER PARK   
198337                         ADMINISTRACCIÓN SEA GARDEN   
198338  ADMINISTRACIÓN DE VILLAS Y HOTEL PIEDRA DEL SO...   
198339   ADMINISTRACION RESIDENCIAL VILLAS PLAYA DIAMANTE   
...                                                   ...   
220848                               VILLAS SAN CRISTOBAL   
220849                                    VILLAS VICTORIA   
220850                                      VILLAS XIMENA   
220868                                  WE HOTEL ACAPULCO   
220872                               WORLDMARK BY WYNDHAM   

                                    raz_social  codigo_act  \
198331                 MOTEL ACAPULCO SA DE CV      721111   
198332                                     NaN      721210   
198337     ALIANZA INTEGRAL TURISTICA SA DE CV      721111   
198338                       HISTORIAS DE LUZ       721190   
198339    PLAYA DIAMANTE RESIDENCIAL VILLAS AC      721190   
...                                        ...         ...   
220848                                     NaN      721190   
220849  SERVICIOS EMPRESARIALES SAN LORENZO SC      721190   
220850                          VILLAS XIMENA       721111   
220868              CABAL DE ACAPULCO SA DE CV      721111   
220872        H &C MANAGEMENT PROFESSIONALS SC      721111   

                                    nombre_act             per_ocu tipo_vial  \
198331  Hoteles con otros servicios integrados    11 a 30 personas   AVENIDA   
198332     Campamentos y albergues recreativos      0 a 5 personas   AVENIDA   
198337  Hoteles con otros servicios integrados  101 a 250 personas     CALLE   
198338             Cabañas, villas y similares      0 a 5 personas   PRIVADA   
198339             Cabañas, villas y similares      0 a 5 personas     CALLE   
...                                        ...                 ...       ...   
220848             Cabañas, villas y similares      0 a 5 personas   AVENIDA   
220849             Cabañas, villas y similares      0 a 5 personas     CALLE   
220850  Hoteles con otros servicios integrados      0 a 5 personas     CALLE   
220868  Hoteles con otros servicios integrados    11 a 30 personas   AVENIDA   
220872  Hoteles con otros servicios integrados    31 a 50 personas     CALLE   

                        nom_vial          tipo_v_e_1  ...  ageb manzana  \
198331     COSTERA MIGUEL ALEMAN               CALLE  ...  1297      25   
198332     FUERZA AEREA MEXICANA               CALLE  ...  5711      29   
198337     COSTERA DE LAS PALMAS  OTRO (ESPECIFIQUE)  ...  1386       1   
198338                   NINGUNO  OTRO (ESPECIFIQUE)  ...  3772     178   
198339     COSTERA DE LAS PALMAS            CIRCUITO  ...  5001       1   
...                          ...                 ...  ...   ...     ...   
220848       PASEO DE LOS HUAJES             CERRADA  ...  0814      32   
220849  PASEO DE LAS GOLONDRINAS               CALLE  ...  1511       1   
220850              LOS GUAYABOS               CALLE  ...  0617       7   
220868     COSTERA MIGUEL ALEMÁN               CALLE  ...  283A      12   
220872    PASEO DE LA MANTARRAYA               CALLE  ...  0585       7   

       telefono                             correoelec  \
198331      NaN           

In [54]:
df["municipio"].unique()    

array(['Acapulco de Juárez', 'Zihuatanejo de Azueta', 'San Marcos',
       'Atoyac de Álvarez', 'Benito Juárez', 'Técpan de Galeana',
       'Petatlán', 'Florencio Villarreal', 'San Miguel Totolapan',
       'Coyuca de Benítez', 'Ajuchitlán del Progreso'], dtype=object)

In [55]:
#Leer shape de municipios
municipios=gpd.read_file("manzanas/conjunto_de_datos/12mun.shp")
#Filtrar municipios 12001, 12002, 12003, 12004, 12005, 12006, 12007, 12008, 12009, 12010, 12011
municipios=municipios[municipios["CVEGEO"].isin(["12001","12003","12011","12014","12021","12030","12038","12048","12053","12054","12057"])]
print(len(municipios))
municipios

11


CVEGEO CVE_ENT CVE_MUN                   NOMGEO  \
0   12001      12     001       Acapulco de Juárez   
2   12003      12     003  Ajuchitlán del Progreso   
10  12011      12     011        Atoyac de Álvarez   
13  12014      12     014            Benito Juárez   
20  12021      12     021        Coyuca de Benítez   
24  12053      12     053               San Marcos   
25  12054      12     054     San Miguel Totolapan   
28  12057      12     057        Técpan de Galeana   
53  12030      12     030     Florencio Villarreal   
61  12038      12     038    Zihuatanejo de Azueta   
71  12048      12     048                 Petatlán   

                                             geometry  
0   MULTIPOLYGON (((2723457.629 539108.729, 272355...  
2   POLYGON ((2646281.417 699141.537, 2646285.940 ...  
10  POLYGON ((2673054.853 617939.844, 2675229.460 ...  
13  POLYGON ((2660209.839 578019.129, 2660264.924 ...  
20  POLYGON ((2702311.467 605759.277, 2702462.899 ...  
24  POLYGON ((2772873.393 563063.802, 2772340.676 ...  
25  POLYGON ((2670470.669 691112.631, 2670510.099 ...  
28  POLYGON ((2631635.945 630369.275, 2632463.311 ...  
53  POLYGON ((2802141.994 537066.283, 2802160.364 ...  
61  MULTIPOLYGON (((2536228.255 632321.838, 253627...  
71  POLYGON ((2589409.415 652144.340, 2590439.224 ...

In [56]:
#Puntos del huracán
puntos=pd.read_csv("https://raw.githubusercontent.com/labdatos-se/economia/main/mapa_gro/dots_otis.csv")
puntos.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 65 entries, 0 to 64
Data columns (total 3 columns):
 #   Column  Non-Null Count  Dtype  
---  ------  --------------  -----  
 0   dot     65 non-null     int64  
 1   lat     65 non-null     float64
 2   long    65 non-null     float64
dtypes: float64(2), int64(1)
memory usage: 1.6 KB


In [107]:
#Leer datos de población y vivienda
pobviv=pd.read_csv("manzanas/RESAGEBURB_12CSV20.csv",encoding="utf-8")
pobviv.columns=[i.lower() for i in pobviv.columns]
#Filtrar municipios 1, 3, 11, 14, 21, 30, 38, 48, 53, 54, 57
pobviv=pobviv[pobviv["mun"].isin([1,3,11,14,21,30,38,48,53,54,57])]
#Dropear ageb 0000
pobviv=pobviv[pobviv["ageb"]!="0000"]
#Dropear nom_loc=="Total AGEB urbana"
pobviv=pobviv[pobviv["nom_loc"]!="Total AGEB urbana"]
#Construir clave geoestadística a nivel manzana. 16 dígitos. Dos por entidad, tres por municipio, cuatro por localidad, tres por ageb, cuatro por manzana
pobviv['cvegeo'] = pobviv['entidad'].astype(str).str.zfill(2) + pobviv['mun'].astype(str).str.zfill(3) + pobviv['loc'].astype(str).str.zfill(4) + pobviv['ageb'].astype(str).str.zfill(4) + pobviv['mza'].astype(str).str.zfill(3)#Añadir columna de largo
pobviv["largo"]=pobviv["cvegeo"].apply(lambda x: len(x))
#Dejar cvgeo y tvivparhab
pobviv=pobviv[["cvegeo","nom_mun", "tvivparhab","pobtot"]]
#Eliminar manzanas sin vivienda o con nan
#Convertir * en nan
pobviv["tvivparhab"]=pobviv["tvivparhab"].replace("*",None)
pobviv["tvivparhab"]=pobviv["tvivparhab"].replace("N/D",None)
pobviv=pobviv[pobviv["tvivparhab"]!=0]
pobviv=pobviv[pobviv['tvivparhab'].notna()]
#Convertir tvivparhab a int
pobviv["tvivparhab"]=pobviv["tvivparhab"].astype(int)
pobviv=pobviv[pobviv["pobtot"].notna()]
#Convertir pobtot a int
pobviv["pobtot"]=pobviv["pobtot"].astype(int)
#Eliminar manzanas sin población
pobviv=pobviv[pobviv["pobtot"]!=0]

#Calcular densidad de población
pobviv["densidad"]=pobviv["pobtot"]/pobviv["tvivparhab"]
pobviv

cvegeo             nom_mun  tvivparhab  pobtot  densidad
4      1200100010034001  Acapulco de Juárez          23      76  3.304348
5      1200100010034002  Acapulco de Juárez          24      80  3.333333
6      1200100010034003  Acapulco de Juárez          22      86  3.909091
7      1200100010034004  Acapulco de Juárez          26     111  4.269231
8      1200100010034005  Acapulco de Juárez          26     102  3.923077
...                 ...                 ...         ...     ...       ...
51588  1205700861216001   Técpan de Galeana           5      24  4.800000
51589  1205700861216800   Técpan de Galeana           7      22  3.142857
51591  1205700861269001   Técpan de Galeana           6      28  4.666667
51592  1205700861269002   Técpan de Galeana           3      12  4.000000
51593  1205700861269800   Técpan de Galeana           7      22  3.142857

[19985 rows x 5 columns]

In [108]:
#obtener el máximo de pobtot 
print("Máximo: ",pobviv["pobtot"].max())
print("Mínimo: ",pobviv["pobtot"].min())

Máximo:  2182
Mínimo:  1


In [123]:
#leer shape de manzanas
manzanas=gpd.read_file("manzanas/conjunto_de_datos/12m.shp")
#Convertir crs a wgs84
manzanas = manzanas.to_crs(epsg=4326)
#Filtrar municipios 001, 003, 011, 014, 021, 030, 038, 048, 053, 054, 057
manzanas=manzanas[manzanas["CVE_MUN"].isin(["001","003","011","014","021","030","038","048","053","054","057"])]
manzanas.columns=[i.lower() for i in manzanas.columns]
#Pegar manzanas con datos de población y vivienda
manzanas=pd.merge(manzanas,pobviv,how="left",on="cvegeo")
#Drop nan
manzanas=manzanas[manzanas['tvivparhab'].notna()]
manzanas=manzanas[manzanas['pobtot'].notna()]
#Calcular área de cada manzana
manzanas["area"]=manzanas.area
#Area a km2
manzanas["area"]=manzanas["area"]/1000000
#Calcular densidad de población
manzanas["densidad"]=manzanas["pobtot"]/manzanas["area"]
#Calcular centroides utilizando los polígonos
manzanas["centroide"]=manzanas.centroid
#Extraer latitud y longitud
manzanas["lat"]=manzanas.centroide.apply(lambda x: x.y)
manzanas["lon"]=manzanas.centroide.apply(lambda x: x.x)
manzanas

C:\Users\claud\AppData\Local\Temp\ipykernel_31912\2001813449.py:19: UserWarning: Geometry is in a geographic CRS. Results from 'area' are likely incorrect. Use 'GeoSeries.to_crs()' to re-project geometries to a projected CRS before this operation.

  manzanas["area"]=manzanas.area
C:\Users\claud\AppData\Local\Temp\ipykernel_31912\2001813449.py:25: UserWarning: Geometry is in a geographic CRS. Results from 'centroid' are likely incorrect. Use 'GeoSeries.to_crs()' to re-project geometries to a projected CRS before this operation.

  manzanas["centroide"]=manzanas.centroid


cvegeo cve_ent cve_mun cve_loc cve_ageb cve_mza  ambito  \
0      1200100013912070      12     001    0001     3912     070  Urbana   
1      1200100010496015      12     001    0001     0496     015  Urbana   
4      1200100016419036      12     001    0001     6419     036  Urbana   
5      1200100016739041      12     001    0001     6739     041  Urbana   
6      1200100016739014      12     001    0001     6739     014  Urbana   
...                 ...     ...     ...     ...      ...     ...     ...   
36201  1205700801288003      12     057    0080     1288     003  Urbana   
36203  1205700011273020      12     057    0001     1273     020  Urbana   
36208  1205700011273021      12     057    0001     1273     021  Urbana   
36212  1205700011273030      12     057    0001     1273     030  Urbana   
36215  1205700011273035      12     057    0001     1273     035  Urbana   

      tipomza                                           geometry  \
0      Típica  POLYGON ((-99.83317 16.91776, -99.83328 16.917...   
1      Típica  POLYGON ((-99.91418 16.83146, -99.91413 16.831...   
4      Típica  POLYGON ((-99.80175 16.82337, -99.80181 16.823...   
5      Típica  POLYGON ((-99.79775 16.83788, -99.79853 16.837...   
6      Típica  POLYGON ((-99.79973 16.83869, -99.79972 16.838...   
...       ...                                                ...   
36201  Típica  POLYGON ((-100.88398 17.27483, -100.88354 17.2...   
36203  Típica  POLYGON ((-100.61774 17.22400, -100.61740 17.2...   
36208  Típica  POLYGON ((-100.62129 17.22575, -100.62091 17.2...   
36212  Típica  POLYGON ((-100.61999 17.22338, -100.61999 17.2...   
36215  Típica  POLYGON ((-100.61784 17.22367, -100.61776 17.2...   

                  nom_mun  tvivparhab  pobtot      densidad          area  \
0      Acapulco de Juárez         6.0    19.0  2.998072e+14  6.337406e-14   
1      Acapulco de Juárez       155.0   487.0  7.671060e+13  6.348536e-12   
4      Acapulco de Juárez         4.0    14.0  1.036956e+14  1.350106e-13   
5      Acapulco de Juárez         6.0    13.0  6.089960e+13  2.134661e-13   
6      Acapulco de Juárez         8.0    19.0  8.742961e+13  2.173177e-13   
...                   ...         ...     ...           ...           ...   
36201   Técpan de Galeana         4.0    12.0  7.076225e+13  1.695819e-13   
36203   Técpan de Galeana         5.0    25.0  6.203996e+13  4.029661e-13   
36208   Técpan de Galeana         8.0    33.0  7.573989e+13  4.357017e-13   
36212   Técpan de Galeana         6.0    20.0  4.463549e+13  4.480740e-13   
36215   Técpan de Galeana         4.0    11.0  6.038470e+13  1.821653e-13   

                         centroide        lat         lon  
0       POINT (-99.83334 16.91764)  16.917640  -99.833340  
1       POINT (-99.91315 16.83160)  16.831600  -99.913153  
4       POINT (-99.80194 16.82384)  16.823842  -99.801942  
5       POINT (-99.79814 16.83803)  16.838033  -99.798136  
6       POINT (-99.80013 16.83857)  16.838571  -99.800131  
...                            ...        ...         ...  
36201  POINT (-100.88370 17.27477)  17.274769 -100.883702  
36203  POINT (-100.61738 17.22444)  17.224441 -100.617385  
36208  POINT (-100.62130 17.22517)  17.225165 -100.621304  
36212  POINT (-100.62012 17.22396)  17.223961 -100.620121  
36215  POINT (-100.61761 17.22366)  17.223655 -100.617612  

[19854 rows x 17 columns]

In [61]:
#Leer shape de marginación
marginacion=gpd.read_file("margina/colonias_imc2020.shp")
marginacion.columns=[i.lower() for i in marginacion.columns]
#Filtrar Guerrero
marginacion=marginacion[marginacion["cve_ent"]=="12"]
#Filtrar municipios 001, 003, 011, 014, 021, 030, 038, 048, 053, 054, 057
marginacion=marginacion[marginacion["mun"].isin(["001","003","011","014","021","030","038","048","053","054","057"])]
marginacion

objectid     cve_col  id_col                              colonia  \
19620     26680  12001_0001   26680                          13 de Junio   
19621     26681  12001_0002   26681                     15 de Septiembre   
19622     26682  12001_0003   26682                          16 de Marzo   
19623     26684  12001_0004   26684  18 de Enero ( Rene Juarez Cisneros)   
19624     26685  12001_0005   26685                      19 de Noviembre   
...         ...         ...     ...                                  ...   
72092    101123  12057_0059  101123                 Luis Donaldo Colosio   
72100    101213  12038_0167  101213                Ejidal Lomas Diamante   
72101    101215  12038_0168  101215                           El Mirador   
72103    101232  12048_0042  101232                          Acapulquito   
72104    101234  12048_0043  101234                        Col Las Tunas   

          cp cve_ent   nom_ent  mun cve_mun                nom_mun  ...  \
19620  39350      12  Guerrero  001   12001     Acapulco de Juárez  ...   
19621  39730      12  Guerrero  001   12001     Acapulco de Juárez  ...   
19622  39350      12  Guerrero  001   12001     Acapulco de Juárez  ...   
19623  39700      12  Guerrero  001   12001     Acapulco de Juárez  ...   
19624  39906      12  Guerrero  001   12001     Acapulco de Juárez  ...   
...      ...     ...       ...  ...     ...                    ...  ...   
72092  40916      12  Guerrero  057   12057      Técpan de Galeana  ...   
72100  40880      12  Guerrero  038   12038  Zihuatanejo de Azueta  ...   
72101  40880      12  Guerrero  038   12038  Zihuatanejo de Azueta  ...   
72103  40831      12  Guerrero  048   12048               Petatlán  ...   
72104  40830      12  Guerrero  048   12048               Petatlán  ...   

            ovpt      ovhac     ovsref     ovsint     ovscel     im_2020  \
19620   0.595107  19.749217   2.204748  28.518277   8.397173  151.140060   
19621   6.125663  34.867727   8.683322  48.359030   7.154946  144.671202   
19622   0.699472  18.116722   1.839302  24.584922   6.883597  151.504738   
19623  18.900593  45.871051   8.628909  75.381911   8.441273  143.677599   
19624  10.162991  45.411915   6.527252  56.999180   7.757499  143.024041   
...          ...        ...        ...        ...        ...         ...   
72092  13.756852  40.923071  16.357628  81.697421  10.071423  140.456136   
72100   0.672976   6.515364   1.565395  23.149782   3.032385  152.887787   
72101   7.053505  42.282849   6.215827  49.559394   3.240741  145.514001   
72103  24.959016  53.965432  15.979283  64.335254  10.030809  134.592117   
72104  18.084380  43.878390   7.526526  60.557631   7.798265  143.583576   

        gm_2020  imn_2020               clasif  \
19620      Bajo  0.963609              Colonia   
19621      Alto  0.922366              Colonia   
19622      Bajo  0.965934  Unidad habitacional   
19623  Muy alto  0.916031              Colonia   
19624  Muy alto  0.911864              Colonia   
...         ...       ...                  ...   
72092  Muy alto  0.895492              Colonia   
72100  Muy bajo  0.974751              Colonia   
72101      Alto  0.927739              Colonia   
72103  Muy alto  0.858106              Colonia   
72104  Muy alto  0.915432               Pueblo   

                                                geometry  
19620  POLYGON ((2725088.770 544549.109, 2725084.445 ...  
19621  POLYGON ((2729889.716 547295.802, 2729809.114 ...  
19622  POLYGON ((2725144.822 543962.973, 2725136.814 ...  
19623  POLYGON ((2731918.486 550107.615, 2731909.035 ...  
19624  POLYGON ((2732711.368 538952.203, 2732725.122 ...  
...                                                  ...  
72092  POLYGON ((2617750.415 588151.638, 2617748.848 ...  
72100  POLYGON ((2547256.542 630427.833, 2547262.262 ...  
72101  POLYGON ((2546576.684 628794.037, 2546556.459 ...  
72103  POLYGON ((2568604.921 619993.043, 2568645.965 ...  
72104  POLYGON ((2579732.108 6

In [62]:
marginacion["gm_2020"].unique()

array(['Bajo', 'Alto', 'Muy alto', 'Medio', 'Muy bajo'], dtype=object)

In [64]:
marginacion.columns

Index(['objectid', 'cve_col', 'id_col', 'colonia', 'cp', 'cve_ent', 'nom_ent',
       'mun', 'cve_mun', 'nom_mun', 'loc', 'cve_loc', 'nom_loc', 'sun_2018',
       'nom_sun', 'pobtot', 'p6a14nae', 'sbasc', 'psdss', 'ovsde', 'ovsee',
       'ovsae', 'ovpt', 'ovhac', 'ovsref', 'ovsint', 'ovscel', 'im_2020',
       'gm_2020', 'imn_2020', 'clasif', 'geometry'],
      dtype='object')

#### Mapa

In [201]:
# color_mapping = {
#     "Muy bajo": "#ffffb2",  # lightest yellow in YlOrRd scheme
#     "Bajo": "#fecc5c",     # light orange
#     "Medio": "#fd8d3c",    # orange
#     "Alto": "#f03b20",     # dark orange/red
#     "Muy alto": "#bd0026"  # darkest red in YlOrRd scheme}

color_mapping = {
    "Muy bajo": "#ffedcc",   # very pale yellow
    "Bajo": "#ffe0b2",      # pale light orange
    "Medio": "#ffcc99",     # pale orange
    "Alto": "#ffa366",      # pale dark orange
    "Muy alto": "#ff7f7f"   # pale red
}


def get_color(feature):
    gm_value = feature['properties']['gm_2020']
    return color_mapping.get(gm_value, '#FFFFFF')

In [209]:
colors = ['#00ff00', '#ffff00', '#ff0000']  # green, yellow, red
cmap = branca.colormap.LinearColormap(colors=colors, vmin=manzanas["pobtot"].min(), vmax=manzanas["pobtot"].max(), caption='Población total')
#Crear mapa de folium con url de google hybrid
mapa=folium.Map(location=[16.85713,-99.88510],zoom_start=12,tiles="https://mt1.google.com/vt/lyrs=s,h&x={x}&y={y}&z={z}",attr="Google Hybrid")
#Añadir shape de municipios. Fondo transparente, contorno naranja. Popup con nombre de municipio
municipio_marker=folium.FeatureGroup(name="Municipios afectados")
folium.GeoJson(municipios,style_function=lambda x: {"fillColor":"#ffffff","color":"#ff9900","weight":3,"fillOpacity":0.1},highlight_function=lambda x: {"fillColor":"#000000","color":"#000000","weight":1,"fillOpacity":0.1},tooltip=folium.GeoJsonTooltip(fields=["NOMGEO"],aliases=["Municipio: "])).add_to(municipio_marker)
municipio_marker.add_to(mapa)


#Agregar circulos de puntos de huracán. Poner como título "Trayectoria del huracán Otis"
for i in range(0,len(puntos)):
    folium.CircleMarker([puntos.iloc[i]["long"],puntos.iloc[i]["lat"]],radius=3,color="red",fill_color="red",fill_opacity=0.2).add_to(mapa)
#Añadir línea de trayectoria del huracán
folium.PolyLine(puntos[["long","lat"]].values.tolist(),color="red",weight=3,opacity=0.5).add_to(mapa)


#Coropletas de marginación
marginacion_group = folium.FeatureGroup(name="Marginación", show=True)

folium.GeoJson(
    marginacion,
    style_function=lambda feature: {
        'fillColor': get_color(feature),
        'fillOpacity': 0.9,
        'color': '#000000',   # You can adjust the border color if needed
        'weight': 1,
        'dashArray': '5, 5'  # Dashed borders, remove this if not desired
    },
    tooltip=folium.GeoJsonTooltip(fields=["nom_mun","colonia", "gm_2020"], aliases=["Municipio","Colonia: ", "Grado de marginación: "], overflow=False, sticky=True),
).add_to(marginacion_group)

marginacion_group.add_to(mapa)


#Heatmap de población. 
heatmap_layer=HeatMap(data=manzanas[["lat","lon","pobtot"]].groupby(["lat",
                                                                "lon"]).sum().reset_index().values.tolist(),
                                                                radius=10,max_zoom=30,gradient={0.0: colors[0], 0.5: colors[1], 1.0: colors[2]},
                                                                overlay=True, control=True,
                                                                name="Población",
                                                                show=True).add_to(mapa)
mapa.add_child(cmap)

#Hoteles

hotel_markers = folium.FeatureGroup(name='Establecimientos de hospedaje',show=False)

for i in range(0,len(df)):
    folium.CircleMarker([df.iloc[i]["latitud"],df.iloc[i]["longitud"]],radius=3,color="#c51b8a",
                        fill_color="#c51b8a",fill_opacity=0.2,popup="<b> Hotel: </b>"+df.iloc[i]["nom_estab"]+"<br><br>"+
                        "<b> Personal ocupado: </b>"+df.iloc[i]["per_ocu"]).add_to(hotel_markers)
hotel_markers.add_to(mapa)

folium.LayerControl(collapsed=False).add_to(mapa)


mapa
#Guardar mapa
mapa.save("gro.html")

In [210]:
mapa